# ロジスティック回帰

## モデル

目的変数$y\in\{0,1\}$の二値分類において、$y=1$である確率を$p$、$y=0$である確率を$1-p$とする。
ロジスティック回帰はそのオッズ比の対数を線形モデルで説明するモデル

$$
\newcommand{\b}[1]{\boldsymbol{#1}}
\log\left( \frac{p}{1-p} \right) = \b{\beta}^\top \b{x}
$$

である。

両辺の指数をとると

$$
p = \frac{ \exp(\b{\beta}^\top \b{x}) }{ 1 + \exp(\b{\beta}^\top \b{x}) }
$$

となる。

:::{dropdown} 導出
$$
\begin{align}
\frac{p}{1-p} &= \exp(\b{\beta}^\top \b{x})\\
\implies
p &= \exp(\b{\beta}^\top \b{x}) (1-p)\\
  &= \exp(\b{\beta}^\top \b{x}) - p \exp(\b{\beta}^\top \b{x})
\end{align}
$$

両辺を$p$で割ると

$$
\begin{align}
1  &= \exp(\b{\beta}^\top \b{x}) \frac{1}{p} - \exp(\b{\beta}^\top \b{x})\\
1 + \exp(\b{\beta}^\top \b{x}) &= \exp(\b{\beta}^\top \b{x}) \frac{1}{p}\\
\implies p &= \frac{ \exp(\b{\beta}^\top \b{x}) }{ 1 + \exp(\b{\beta}^\top \b{x}) }
\end{align}
$$
:::

この$p$はロジスティック・シグモイド関数

$$
\sigma(z) = \frac{\exp(z)}{1 + \exp(z)}
= \frac{1}{1 + \exp(-z)}
$$

と呼ばれる、$(-\infty, \infty)$の入力を$(0, 1)$に変換する関数である。


:::{dropdown} 導出
TODO
$$
\frac{ \exp(z) }{ 1+\exp(z) }
$$

:::

## 誤差関数

ロジスティック回帰は、統計学的な言い方だと最尤推定法でパラメータを推定する。

機械学習的な言い方をすると交差エントロピー誤差を最小化するようにパラメータを推定する。


### ベルヌーイ分布

ロジスティック回帰は$P(y=1) = p, P(y = 0) = 1-p$のベルヌーイ分布に従う。

$$
P(y) = \begin{cases}
p & \text{if } y = 1\\
1-p & \text{if } y = 0
\end{cases}
$$

この確率質量関数は一括で書くと

$$
P(Y=y) = p^y (1 - p)^{1-y}
$$

と書くことができる。

### 尤度関数

尤度関数$L(\theta)$とは一般に確率(密度/質量)関数$f(x| \theta)$の積

$$
L(\theta) = \prod^n_{i=1} f(x_i| \theta)
$$

である（独立に得られたサンプルを仮定するので単純な積が同時確率を意味する）。

そのため、ベルヌーイ分布の尤度関数は

$$
L(p) = \prod^n_{i=1} p^{y_i} (1 - p)^{1- y_i}
$$

となる。

ロジスティック回帰で使う場合、$p \in [0, 1]$はロジスティック回帰の予測値$p_i=\sigma(\beta^\top x_i)$、$y \in \{0, 1\}$は実測値である。

$$
L(\beta) = \prod^n_{i=1} p_i^{y_i} (1 - p_i)^{1- y_i}
$$

### 交差エントロピー誤差

尤度関数の対数を取って符号を負に反転させたものを**交差エントロピー誤差**（cross entropy loss）という。log lossやlogistic lossとも呼ばれる

$$
\mathcal{L}(\beta) = -\ln L(\beta)
= -\sum^n_{i=1} \{ y_i \ln p_i + (1 - y_i) \ln (1 - p_i) \}
$$




### 勾配

交差エントロピーの勾配は

$$
\nabla \mathcal{L}(\beta)
= \frac{ \partial \mathcal{L}(\beta) } { \partial \beta }
= \sum^n_{i=1} (p_i - y_i) x_i
$$

:::{dropdown} 導出
総和を取るまえの1レコード単位のものを使う。

$$
\newcommand{\s}{ \sigma(\beta^\top x) }
\ell(\beta) = y \ln \s + (1 - y) \ln (1 - \s)
$$

$\s$に関する微分

$$
\begin{align}
\frac{d \ln \s}{d \beta}
&= \frac{d \ln \s}{d \s} \frac{d \s}{d (\beta^\top x)} \frac{d (\beta^\top x)}{d \beta}\\
&= \frac{1}{\s} \cdot \s (1 - \s) \cdot x\\
&= 1 - \s x
\\
\frac{d \ln (1 -\s)}{d \beta}
&= \frac{d \ln (1 -\s)}{d \s} \frac{d \s}{d (\beta^\top x)} \frac{d (\beta^\top x)}{d \beta}\\
&= -\frac{1}{1-\s} \cdot \s (1 - \s) \cdot x\\
&= - \s x
\end{align}
$$

より、

$$
\begin{align}
\frac{d \ell(\beta)}{d\beta}
&= y (1 - \s)x - (1 - y) \s x\\
&= (y - y\s - \s + y\s) x\\
&= (y - \s ) x\\
\end{align}
$$


（参考）使った微分

$$
\begin{align}
\frac{d \log x}{dx} &= \frac{1}{x}\\
\frac{d \sigma(x)}{dx} &= \sigma(x) (1- \sigma(x))\\
\frac{d \sigma(\beta^\top x)}{dx} &= \frac{d \sigma(\beta^\top x)}{d(\beta^\top x)} \times \frac{d (\beta^\top x)}{dx}
= \sigma(\beta^\top x) (1- \sigma(\beta^\top x)) \times x \\
\end{align}
$$

:::

## $y \in \{-1, 1\}$にする場合

上記の例では$y \in \{0, 1\}$としていた。$y\in \{-1, 1\}$とする場合は少し書き方が変わる

$y=1$の確率と$y=-1$の確率がそれぞれ

$$
\begin{align}
p(y=1|x) &= \frac{\exp(\beta^\top x)}{1 + \exp(\beta^\top x)}
  = \frac{ 1 }{1 + \exp(- \beta^\top x)}\\
p(y=-1|x) &= 1 - p(y=1|x)\\
  &= \frac{ 1 + \exp(\beta^\top x)}{1 + \exp(\beta^\top x)} - \frac{\exp(\beta^\top x)}{1 + \exp(\beta^\top x)}
  = \frac{ 1 }{1 + \exp(\beta^\top x)}\\
\end{align}
$$

で表されるとする。$y\in \{-1, 1\}$のとき、これらを1つにまとめて、$y$の確率を

$$
p(y|x) = \frac{1}{1 + \exp(- y \beta^\top x )}
$$

と書くことができる。

尤度は

$$
\prod^n_{i=1} \frac{1}{1 + \exp(- y_i \beta^\top x_i )}
$$

負の対数尤度は

$$
\sum^n_{i=1} \log \big( 1 + \exp(- y_i \beta^\top x_i ) \big)
$$

と書くことができる。機械学習の分野だとこちらの表現のほうが目にするかも。

:::{margin}
$$
\log \frac{M}{N} = \log M - \log N
$$

のため

$$
\begin{align}
\log \frac{1}{1 + \exp(- y_i \beta^\top x_i )}
= \log 1 - \log (1 + \exp(- y_i \beta^\top x_i ))\\
= 0 - \log (1 + \exp(- y_i \beta^\top x_i ))
\end{align}
$$
:::

## 線形分離可能性

機械学習として（目的変数の予測が目的）のロジスティック回帰では、線形分離可能な問題であることが嬉しい

統計学としては最尤推定量が存在しない（解が一意に定まらない）という扱いになる様子

- [ロジスティック回帰に最尤推定量が存在するか判定する - ほくそ笑む](https://hoxo-m.hatenablog.com/entry/2024/02/26/210225)
